In [3]:
import pandas as pd
import numpy as np
import sklearn
from sklearn.model_selection import train_test_split
from sklearn.metrics import accuracy_score

from sklearn.metrics import confusion_matrix 

from sklearn import tree
from matplotlib import pyplot as plt 
import random
from sklearn import preprocessing

import warnings
from sklearn.exceptions import DataConversionWarning
warnings.filterwarnings(action='ignore', category=DataConversionWarning)
pd.set_option('mode.chained_assignment', None)

import pydotplus

In [4]:
pd.set_option('display.max_columns', 500)


In [5]:
def run_single_geography_model(data_df, predict_df, df_cols, predict_cols, name):
    """
    Note that predict_cols[0] must be equal to the binary gentrification varible
    """
    # drop na
    d = {}
    for i in predict_cols:
        d[i] = predict_df[i]
    # merge into new df
    df = data_df.join(pd.DataFrame(
        #index="geo_fips",
        data=d
    ))
    s = df.shape
    df = df.dropna()
    print("previous to dropping", s, "after dropping", df.shape)
    new_predict = pd.DataFrame()
    for i in predict_cols:
        new_predict[i] = df[i]
    del data_df
    # new data_df
    data_df = pd.DataFrame()
    for i in df_cols + ["geo_fips"]:
        data_df[i] = df[i]
    print(new_predict.shape, data_df.shape)
    assert new_predict.shape[0] == data_df.shape[0], "after removing nulls, predict and data don't have the same # of rows"
    # normal
    for i in predict_cols:
        print("=============================================================")
        if "disp" in i.lower():
            print(i, "regression")
            model, stats = train_model(data_df[df_cols], new_predict, df_cols, i, "regression")
            diff = stats.loc[(stats['diff'] >= stats["diff"].quantile(0.01)) & (stats['diff'] <= stats["diff"].quantile(0.99))]["diff"]
            print("description")
            print(stats['diff'].describe())
            #plt.hist(stats["diff"])
            plt.hist(diff)
            plt.show()
        else:
            print(i, "classification")
            model, stats, confusion_matrix = train_model(data_df[df_cols], new_predict, df_cols, i, "classification")
            print("accuracy score", stats)
            print("confusion matrix")
            print(confusion_matrix)
            output_csv(model, data_df, df_cols, new_predict[i], "Normal set", name)
    # equal number of gentrified and non-gent geometries 
    original_data = data_df.copy()
    original_predict = new_predict.copy()
    temp_table = data_df.copy()
    temp_table[predict_cols[0]] = new_predict[predict_cols[0]]
    temp_table = temp_table.loc[temp_table[predict_cols[0]] == 1]
    gent_indicies = temp_table.index
    other_indicies = set(data_df.index) - set(gent_indicies)
    non_gent_selected_indicies = random.sample(list(other_indicies), len(gent_indicies))
    assert len(non_gent_selected_indicies) == len(gent_indicies), "gent data is not split 50/50"
    print(list(non_gent_selected_indicies)[:5], type(non_gent_selected_indicies), type(gent_indicies))
    gent_indicies = list(gent_indicies)
    data_df = data_df.loc[non_gent_selected_indicies + gent_indicies]
    new_predict = new_predict.loc[non_gent_selected_indicies + gent_indicies]
    #validation = 
    print("=============================================================")
    print("=============================================================")
    print("=============================================================")
    print("=====================50/50 split=============================")
    for i in predict_cols:
        print("=============================================================")
        if "disp" in i.lower():
            print(i, "regression", "50/50 split")
            model, stats = train_model(data_df[df_cols], new_predict, df_cols, i, "regression")
            diff = stats.loc[(stats['diff'] >= stats["diff"].quantile(0.01)) & (stats['diff'] <= stats["diff"].quantile(0.99))]["diff"]
            print("description")
            print(stats['diff'].describe())
            #plt.hist(stats["diff"])
            plt.hist(diff)
            plt.show()
        else:
            print(i, "classification" , "50/50 split")
            model, stats, confusion_matrix = train_model(data_df[df_cols], new_predict, df_cols, i, "classification")
            print("accuracy score", stats)
            print("confusion matrix")
            print(confusion_matrix)
            output_csv(model, original_data, df_cols, original_predict[i], "Even split" ,name)

        

In [6]:
def optimize_classification(x1_train, y1_train):
    def helper(depth):
        #clf = tree.DecisionTreeClassifier(max_depth=50, criterion="entropy")
        clf = tree.DecisionTreeClassifier(max_depth=depth, criterion="entropy")
        clf = clf.fit(x1_train, y1_train)
        z = clf.predict(x1_train)
        stats = accuracy_score(z, y1_train)
        matrix = confusion_matrix(y1_train, z) 
        return clf, stats, matrix
    max_depth = None
    clf = None
    max_accuracy = 0
    max_determinant = 0
    for i in range(10,50,5):
        model, acc, matrix = helper(i)
        #if acc > max_accuracy:
        det = np.linalg.det(matrix)
        if det > max_determinant:
            clf = model
            max_accuracy = acc
            max_depth = i
            max_determinant = det
    return clf, max_depth
    

In [7]:
def optimize_regression(x1_train, y1_train):
    def helper(depth):
        clf = tree.DecisionTreeRegressor(max_depth=depth, criterion="entropy")
        clf = clf.fit(x1_train, y1_train)
        z = clf.predict(x1_train)
        stats = accuracy_score(z, y1_train)
        matrix = confusion_matrix(y1_train, z) 
        return clf, stats, matrix
    max_depth = None
    clf = None
    max_accuracy = 0
    max_determinant = 0
    for i in range(10,50,5):
        model, acc, matrix = helper(i)
        #if acc > max_accuracy:
        det = np.linalg.det(matrix)
        if det > max_determinant:
            clf = model
            max_accuracy = acc
            max_depth = i
            max_determinant = det
    return clf, max_depth
    

In [8]:
def train_model(df, predict_df, df_cols, predict_col, model_type):
    min_max_scaler = preprocessing.MinMaxScaler()
    df_norm = pd.DataFrame(min_max_scaler.fit_transform(df), columns=df_cols)
    X = df_norm
    Y = predict_df[predict_col]
    #x1_train, x1_val, y1_train, y1_val = train_test_split(X, Y, test_size=0.30)
    x1_train, x1_val, y1_train, y1_val = train_test_split(X, Y, test_size=0.33, random_state=42)
    print("size of training set", str(y1_train.shape), "size of testing set", len(y1_val), "original", str(Y.shape))
    # clean Data
    x1_train, y1_train = clean_data(x1_train, y1_train)
    
    if model_type == "regression":
        clf = tree.DecisionTreeRegressor() # max_depth=50
        #clf = clf.fit(x1_train._get_numeric_data(), y1_train)
        clf = clf.fit(x1_train, y1_train)
        #clf, max_depth = optimize_regression(x1_train, y1_train)
        z = clf.predict(x1_val)
        stats = pd.DataFrame({"predicted": z, "actual": y1_val, "diff": (y1_val - z)})
        return clf, stats
    else:
        #clf = tree.DecisionTreeClassifier(max_depth=50, criterion="entropy")
        #clf = clf.fit(x1_train, y1_train)
        clf, max_depth = optimize_classification(x1_train, y1_train)
        z = clf.predict(x1_val)
        #tree.plot_tree(clf)
        from sklearn.externals.six import StringIO  
        from IPython.display import Image  
        from sklearn.tree import export_graphviz
        import pydotplus
        dot_data = StringIO()
        export_graphviz(clf, out_file=dot_data,  
                        filled=True, rounded=True,
                        special_characters=True)
        graph = pydotplus.graph_from_dot_data(dot_data.getvalue())  
        display(Image(graph.create_png()))
        
        stats = accuracy_score(z, y1_val)
        confusion = confusion_matrix(y1_val, z) 
        return clf, stats, confusion

In [9]:
def confusion(a, b):
    """
    a must be from data, b must be from model
    """
    assert a in [0, 1] and b in [0, 1], "not binary 0/1"
    if a and b:
        #print("TP")
        return 0
    elif a and not b:
        #print("FN")
        return 1
    elif not a and b:
        #print("FP")
        return 2
    elif not a and not b:
        #print("TN")
        return 3

In [10]:
def output_csv(clf, data, df_cols, predict, split_type, name):
    z = clf.predict(data[df_cols])
    #stats = accuracy_score(z, predict)
    #print(data.columns)
    #fips = data["geo_fips"]
    #print(data["geo_fips"])
    df = pd.DataFrame({"actual": predict, "predicted": z, "geo_fips": data["geo_fips"]})
    arr = []
    for index, row in df.iterrows():
        #print(row.get("geo_fips"))
        #print(df.loc[index,'Qty'] == 1)
        """
        val = None;
        TP = df.loc[index,'actual'] == 1 and df.loc[index,'predicted'] == 1 #np.sum(np.logical_and(pred_labels == 1, true_labels == 1))
        TN = df.loc[index,'actual'] == 0 and df.loc[index,'predicted'] == 0
        #np.sum(np.logical_and(pred_labels == 0, true_labels == 0))
        FP = df.loc[index,'actual'] == 1 and df.loc[index,'predicted'] == 0
        #np.sum(np.logical_and(pred_labels == 1, true_labels == 0))
        FN = df.loc[index,'actual'] == 0 and df.loc[index,'predicted'] == 1
        #np.sum(np.logical_and(pred_labels == 0, true_labels == 1))
        if TP:
            val = 0
        elif TN:
            val = 3
        elif FP:
            val = 2
        elif FN:
            val = 1
        arr.append(val)
        """
        arr.append(confusion(df.loc[index,'actual'], df.loc[index,'predicted']))
    df["false_positive"] = arr
    
    df.to_csv("output/" + name + " " + split_type + ".csv")

In [11]:
def clean_data(x_train, y_train):
    #print(type(x_train), type(y_train))
    x_train["y_train"] = y_train
    first = x_train["y_train"].quantile(0.1)
    second = x_train["y_train"].quantile(0.9)
    df = x_train.loc[(x_train['y_train'] >= first) & (x_train['y_train'] <= second)]
    #print(df.columns)
    y_train = df["y_train"]
    df = df.drop(columns=["y_train"])
    return df, y_train

In [12]:
def stack_data(df1, cols1, df2, cols2, predict, predict_cols1, predict_cols2):
    assert len(cols1) == len(cols2), "input sizes are not the same"
    df1 = df1[cols1]
    df2 = df2[cols2]
    stacked_data = np.vstack((df1.values, df2.values))
    predict1 = predict[predict_cols1]
    predict2 = predict[predict_cols2]
    stacked_predict = np.vstack((predict1.values, predict2.values))
    stacked_data = pd.DataFrame(stacked_data, columns=cols1)
    stacked_predict = pd.DataFrame(stacked_predict, columns=predict_cols1)
    return stacked_data, stacked_predict

In [13]:
def stack_data_diff_geographies(df1, cols1, df2, cols2, predict1, predict2, predict_cols1, predict_cols2):
    assert len(cols1) == len(cols2), "input sizes are not the same"
    df1 = df1[cols1]
    df2 = df2[cols2]
    stacked_data = np.vstack((df1.values, df2.values))
    predict1 = predict1[predict_cols1]
    predict2 = predict2[predict_cols2]
    stacked_predict = np.vstack((predict1.values, predict2.values))
    stacked_data = pd.DataFrame(stacked_data, columns=cols1)
    stacked_predict = pd.DataFrame(stacked_predict, columns=predict_cols1)
    return stacked_data, stacked_predict

# Collumn Data for all the locations and years

In [14]:
ny_00_cols = ["TOD", "downtown", "per_asian_00", "mhval00", "empd02", "hh00", "hinc00", "hu_00", "per_black_00", "per_built_90_00", "per_car_commute_00", "per_col00", "per_hhwchild_00", "per_latino_00", "per_nonwhite00", "per_owners_00", "per_rent00", "per_units_pre50", "pop00"]
ny_90_cols = ["TOD", "downtown", "per_asian_90", "mhval90", "empd02", "hh_90", "hinc90", "hu_90", "per_black_90", "per_built_80_90", "per_car_commute_90", "per_col90", "per_hhwchild_90", "per_latino_90", "per_nonwhite90", "per_owners_90", "per_rent90", "per_units_pre50", "pop90"]

sf_00_cols = ["tod", "downtown", "per_asian00", "mhval00", "emp_density00", "hh00", "hinc00", "hu00", "per_nhblk00", "per_built90_00", "per_carcommute00", "per_col00", "per_hhwchild00", "per_hisp00", "per_nonwhite00", "per_own00", "per_rent00", "per_units_pre50_00", "pop00"]
sf_90_cols = ["tod", "downtown", "per_asian90", "mhval90", "emp_density90", "hh90", "hinc90", "hu90", "per_nhblk90", "per_built80_90", "per_carcommute90", "per_col90", "per_hhwchild90", "per_hisp90", "per_nonwhite90", "per_own90", "per_rent90", "per_units_pre50_90", "pop90"]

In [15]:
ny_00_df = pd.read_excel("UDP_NY_2016_7.13.19_selectedNYNJcounties.xlsx", sheet_name="2000 data")
ny_90_df = pd.read_excel("UDP_NY_2016_7.13.19_selectedNYNJcounties.xlsx", sheet_name="1990 data")

sf_00_df = pd.read_excel("UDP_SF_2015_6.6.19.xlsx", sheet_name="2000 data")
sf_90_df = pd.read_excel("UDP_SF_2015_6.6.19.xlsx", sheet_name="1990 data")


to_predict_ny = pd.read_excel("UDP_NY_2016_7.13.19_selectedNYNJcounties.xlsx", sheet_name="to predict")
# put these 2 collumn value lists in the same order
predict_ny_90_cols = ["gent90_00", "Disp_index_90_00_count", "Disp_index_90_00_pctch_count", "Disp_index_90_00_pctch_per"]
predict_ny_00_cols = ["gent00_16", "Disp_index_00_16_count", "Disp_index_00_15_pctch_count", "Disp_index_00_15_pctch_per"]

predict_sf_90_cols = ["gent90_00_v2", "Disp_index_90_00_count", "Disp_index_90_00_pctch_count", "Disp_index_90_00_pctch_per"]
predict_sf_00_cols = ["gent00_15_v2", "Disp_index_00_15_count", "Disp_index_00_15_pctch_count", "Disp_index_00_15_pctch_per"]

to_predict_sf = pd.read_excel("UDP_SF_2015_6.6.19.xlsx", sheet_name="to predict")
#predict_ny_00_cols = ["gent00_15_v2", "Disp_index_90_00_count", "Disp_index_90_00_pctch_count", "Disp_index_90_00_pctch_per", "Disp_index_00_15_count", "Disp_index_00_15_pctch_count", "Disp_index_00_15_pctch_per", "Gent_index_90_00", "Gent_index_00_15"]


# 1990s NY

In [16]:
run_single_geography_model(ny_90_df, to_predict_ny, ny_90_cols, predict_ny_90_cols, "1990s NY")

previous to dropping (3852, 26) after dropping (3066, 26)
(3066, 4) (3066, 20)
gent90_00 classification
size of training set (2054,) size of testing set 1012 original (3066,)


InvocationException: GraphViz's executables not found

# 2000s NY

In [ ]:
run_single_geography_model(ny_00_df, to_predict_ny, ny_00_cols, predict_ny_00_cols, "2000s Ny")

# Stacking decades of NY Data

In [ ]:
df_data, df_predict = stack_data(ny_00_df, ny_00_cols + ["geo_fips"], ny_90_df, ny_90_cols + ["geo_fips"], to_predict_ny, predict_ny_00_cols, predict_ny_90_cols)

print(type(df_data), type(df_predict), df_data.columns)


In [ ]:
run_single_geography_model(df_data, df_predict, ny_00_cols, predict_ny_00_cols, "NY Stacked Decades")

# 1990s SF

In [ ]:
run_single_geography_model(sf_90_df, to_predict_sf, sf_90_cols, predict_sf_90_cols, "1990s SF")

# 2000s SF

In [ ]:
run_single_geography_model(sf_00_df, to_predict_sf, sf_00_cols, predict_sf_00_cols, "2000s SF")

# Stacking decades of SF Data

In [ ]:
df_data, df_predict = stack_data(sf_00_df, sf_00_cols  + ["geo_fips"], sf_90_df, sf_90_cols + ["geo_fips"], to_predict_sf, predict_sf_00_cols, predict_sf_90_cols)

print(type(df_data), type(df_predict))


In [ ]:
run_single_geography_model(df_data, df_predict, sf_00_cols, predict_sf_00_cols, "SF Stacked Decades")

# Stacking SF and NY data from 90s

In [ ]:
df_data, df_predict = stack_data_diff_geographies(sf_90_df, sf_90_cols + ["geo_fips"], ny_90_df, ny_90_cols + ["geo_fips"], to_predict_sf, to_predict_ny, predict_sf_90_cols, predict_ny_90_cols)

print(type(df_data), type(df_predict), df_predict.columns)


In [ ]:
run_single_geography_model(df_data, df_predict, sf_90_cols, predict_sf_90_cols, "SF_NY 90s")

# Stacking SF and NY data from 00s

In [ ]:
df_data, df_predict = stack_data_diff_geographies(sf_00_df, sf_00_cols + ["geo_fips"], ny_00_df, ny_00_cols + ["geo_fips"], to_predict_sf, to_predict_ny, predict_sf_00_cols, predict_ny_00_cols)

print(type(df_data), type(df_predict), df_predict.columns)


In [ ]:
run_single_geography_model(df_data, df_predict, sf_00_cols, predict_sf_00_cols, "SF_NY 00s")

# Mixing up all of the Data

In [ ]:
df_data_90, df_predict_90 = stack_data_diff_geographies(sf_90_df, sf_90_cols + ["geo_fips"], ny_90_df, ny_90_cols + ["geo_fips"], to_predict_sf, to_predict_ny, predict_sf_90_cols, predict_ny_90_cols)
df_data_00, df_predict_00 = stack_data_diff_geographies(sf_00_df, sf_00_cols + ["geo_fips"], ny_00_df, ny_00_cols + ["geo_fips"], to_predict_sf, to_predict_ny, predict_sf_00_cols, predict_ny_00_cols)
df_data, df_predict = stack_data_diff_geographies(df_data_90, sf_90_cols + ["geo_fips"], df_data_00, sf_00_cols + ["geo_fips"], df_predict_90, df_predict_00, predict_sf_90_cols, predict_sf_00_cols)


In [ ]:
run_single_geography_model(df_data, df_predict, sf_90_cols, predict_sf_90_cols, "SF_NY Mixed Decades")

In [16]:
memphis_data = pd.read_stata('clean_Memphis_merge_081319.dta')

In [17]:
memphis_data



trtid10        hinc_00       pop_00   nhwhite_00     nhblk_00  \
0    28033070101   26255.709055  2252.779795  1744.566281   321.876895   
1    28033070102   34183.920552  2933.442759  2271.636352   419.144058   
2    28033070210   79501.087837  2821.094333  2594.073051   134.013479   
3    28033070221   42015.009727  3534.000000  2993.304836   402.616248   
4    28033070222   19446.971405  1635.739165  1385.474237   186.354036   
5    28033070310   57698.443809  2737.000000  2448.000000   108.000000   
6    28033070322   58913.163057  2986.000000  2545.000000   129.000000   
7    28033070323   17604.728319  3485.094249  2807.745484   486.198660   
8    28033070324   24204.421468  4794.203911  3862.079274   669.163833   
9    28033070325   15830.067217  3135.483749  2525.859773   437.643530   
10   28033070411   18057.463635  1661.000000  1344.252540   216.986812   
11   28033070412   42942.192270  3950.000000  3196.747460   516.013188   
12   28033070421   27299.415126  2617.522172  2474.480115     8.847962   
13   28033070422   28219.022141  2705.695920  2557.835354     9.146014   
14   28033070520   89312.845116  4088.000000  3770.000000   224.000000   
15   28033070521   31678.904839  3775.004999  3440.962864   165.846517   
16   28033070522   35748.820539  4259.995001  3883.037136   187.153483   
17   28033070610   73442.242746  1585.000000  1567.000000     0.000000   
18   28033070620   92957.002861  3006.000000  2631.000000   326.000000   
19   28033070630   92817.450009  4225.260835  3516.220927   639.029716   
20   28033070710   87636.646772  3799.988740  3188.412843   539.639911   
21   28033070721   39375.488447  2556.011260  2062.956078   454.125807   
22   28033070722   38552.801438  2505.000000  2021.631079   445.234282   
23   28033070811   50734.363193  3574.708494  3112.389147   336.669485   
24   28033070812   33812.621083  2388.739643  2080.390685   224.476788   
25   28033070821   36427.938704  3842.594239  3464.288855   261.648432   
26   28033070822   38035.140773  4012.957625  3617.931312   273.205295   
27   28033070830   90335.918267  2359.000000  1800.000000   476.000000   
28   28033070900   67822.254379  3659.906550  2722.930475   890.977250   
29   28033071000   83919.546521  4798.691387  4226.847330   466.872683   
..           ...            ...          ...          ...          ...   
241  47157021745   97546.540366  6782.632580  3097.024404  3378.391309   
242  47157021746   37719.524914  4470.000000  1756.574799  2484.261357   
243  47157021747   34538.258495  4093.000000  1608.425201  2274.738643   
244  47157021751  108909.739273  3900.000000  1469.000000  2130.000000   
245  47157021752  103310.214957  1867.000000   727.000000  1131.000000   
246  47157021753   77851.543931  3213.000000  1158.000000  1745.000000   
247  47157021754   86700.406212  4402.000000  1512.000000  2502.000000   
248  47157021900   57704.207601  5708.000000   197.000000  5489.000000   
249  47157022022   30383.831631  7822.000000   203.000000  7146.000000   
250  47157022023   25694.713181  4486.000000   222.262593  4184.357910   
251  47157022024   22859.473987  3991.000000   197.737407  3722.642090   
252  47157022111   38607.322436  6574.000000   382.000000  6053.000000   
253  47157022112   40986.327748  6705.000000   265.000000  6335.000000   
254  47157022121   31321.209113  4411.000000   377.024822  3980.182495   
255  47157022122   34473.922068  4855.000000   414.975178  4380.817505   
256  47157022130   58698.461790  6448.000000   485.000000  5874.000000   
257  47157022210   43647.747529  5179.998652    87.999977  5013.998695   
258  47157022220   33399.747363  4688.001348   117.000023  4566.001305   
259  47157022310   34205.225991  6365.000000    22.000000  6317.000000   
260  47157022321   46662.222313  3846.000000   138.000000  3708.000000   
261  47157022322   62101.981201  4724.000000    78.000000  4597.000000   
262  47157022330   44659.304454  5670.000000   103.000000  5343.000000   
263  47157022

In [ ]:
pd.Series(df.columns).values


In [20]:
mem_type = pd.read_csv('typology_input.csv')

In [21]:
mem_type

Unnamed: 0         FIPS  COUNTYFP  \
0             0  47157000200       157   
1             1  47157000800       157   
2             2  47157003500       157   
3             3  47157005900       157   
4             4  47157007500       157   
5             5  47157009500       157   
6             6  47157011700       157   
7             7  47157020521       157   
8             8  47157020542       157   
9             9  47157021112       157   
10           10  47157021312       157   
11           11  47157021530       157   
12           12  47157021724       157   
13           13  47157022130       157   
14           14  47157022321       157   
15           15  47157000300       157   
16           16  47157000400       157   
17           17  47157000700       157   
18           18  47157001900       157   
19           19  47157002600       157   
20           20  47157003300       157   
21           21  47157004600       157   
22           22  47157006400       157   
23           23  47157007400       157   
24           24  47157007900       157   
25           25  47157008700       157   
26           26  47157009800       157   
27           27  47157010610       157   
28           28  47157010620       157   
29           29  47157011200       157   
..          ...          ...       ...   
202         202  47157007100       157   
203         203  47157020642       157   
204         204  47157020820       157   
205         205  47047060800        47   
206         206  47157002500       157   
207         207  47157004200       157   
208         208  47157007000       157   
209         209  47157008600       157   
210         210  47157010220       157   
211         211  47157020511       157   
212         212  47157020832       157   
213         213  47157021753       157   
214         214  47157022322       157   
215         215  47157008120       157   
216         216  47157009400       157   
217         217  47157010210       157   
218         218  47157020634       157   
219         219  47157021020       157   
220         220  47157021137       157   
221         221  47157021200       157   
222         222  47157021613       157   
223         223  47157021744       157   
224         224  47157022410       157   
225         225  47047060404        47   
226         226  47157002700       157   
227         227  47157020632       157   
228         228  47157020644       157   
229         229  47157010720       157   
230         230  47157021113       157   
231         231  47047060402        47   

                                              geometry        hinc_00  \
0    POLYGON ((-90.049055 35.16613299999999, -90.04...   11361.875766   
1    POLYGON ((-89.98362499999999 35.174497, -89.98...   22039.301185   
2    POLYGON ((-90.021001 35.129804, -90.0208289999...   67319.654271   
3    POLYGON ((-90.047072 35.11587, -90.040992 35.1...   20340.070142   
4    POLYGON ((-90.03931399999999 35.097482, -90.03...   36268.663670   
5    POLYGON ((-89.896181 35.112915, -89.888634 35....   64396.625066   
6    POLYGON ((-90.076611 35.122858, -90.073865 35....  104057.833269   
7    POLYGON ((-89.968761 35.254472, -89.964911 35....   39850.860646   
8    POLYGON ((-89.922054 35.203085, -89.9217889999...   42068.479771   
9    POLYGON ((-89.83940799999999 35.200551, -89.83...   60271.977115   
10   POLYGON ((-89.84225699999999 35.107646, -89.84...   28865.884726   
11   POLYGON ((-89.73248699999999 35.051867, -89.73...  146462.287699   
12   POLYGON ((-89.84393299999999 35.055673, -89.84...   58591.831631   
13   POLYGON ((-90.035231 35.006369, -90.0271229999...   58698.461790   
14   POLYGON ((-90.07322099999999 35.035397, -90.06...   46662.222313   
15   POLYGON ((-90.03621699999999 35.16754, -90.036...   17312.991418   
16   POLYGON ((-90.024981 35.174556, -90.023994 35....   18998.900695   
17   POLYGON ((-90.010195 35.168159, -90.0089819999...   32499.143441   
18   POLYGON 

In [22]:
memphis = pd.read_stata('memphis_typology_081319.dta')

In [23]:
memphis

trtid10        hinc_00       pop_00   nhwhite_00     nhblk_00  \
0    28033070101   26255.709055  2252.779795  1744.566281   321.876895   
1    28033070102   34183.920552  2933.442759  2271.636352   419.144058   
2    28033070210   79501.087837  2821.094333  2594.073051   134.013479   
3    28033070221   42015.009727  3534.000000  2993.304836   402.616248   
4    28033070222   19446.971405  1635.739165  1385.474237   186.354036   
5    28033070310   57698.443809  2737.000000  2448.000000   108.000000   
6    28033070322   58913.163057  2986.000000  2545.000000   129.000000   
7    28033070323   17604.728319  3485.094249  2807.745484   486.198660   
8    28033070324   24204.421468  4794.203911  3862.079274   669.163833   
9    28033070325   15830.067217  3135.483749  2525.859773   437.643530   
10   28033070411   18057.463635  1661.000000  1344.252540   216.986812   
11   28033070412   42942.192270  3950.000000  3196.747460   516.013188   
12   28033070421   27299.415126  2617.522172  2474.480115     8.847962   
13   28033070422   28219.022141  2705.695920  2557.835354     9.146014   
14   28033070520   89312.845116  4088.000000  3770.000000   224.000000   
15   28033070521   31678.904839  3775.004999  3440.962864   165.846517   
16   28033070522   35748.820539  4259.995001  3883.037136   187.153483   
17   28033070610   73442.242746  1585.000000  1567.000000     0.000000   
18   28033070620   92957.002861  3006.000000  2631.000000   326.000000   
19   28033070630   92817.450009  4225.260835  3516.220927   639.029716   
20   28033070710   87636.646772  3799.988740  3188.412843   539.639911   
21   28033070721   39375.488447  2556.011260  2062.956078   454.125807   
22   28033070722   38552.801438  2505.000000  2021.631079   445.234282   
23   28033070811   50734.363193  3574.708494  3112.389147   336.669485   
24   28033070812   33812.621083  2388.739643  2080.390685   224.476788   
25   28033070821   36427.938704  3842.594239  3464.288855   261.648432   
26   28033070822   38035.140773  4012.957625  3617.931312   273.205295   
27   28033070830   90335.918267  2359.000000  1800.000000   476.000000   
28   28033070900   67822.254379  3659.906550  2722.930475   890.977250   
29   28033071000   83919.546521  4798.691387  4226.847330   466.872683   
..           ...            ...          ...          ...          ...   
241  47157021745   97546.540366  6782.632580  3097.024404  3378.391309   
242  47157021746   37719.524914  4470.000000  1756.574799  2484.261357   
243  47157021747   34538.258495  4093.000000  1608.425201  2274.738643   
244  47157021751  108909.739273  3900.000000  1469.000000  2130.000000   
245  47157021752  103310.214957  1867.000000   727.000000  1131.000000   
246  47157021753   77851.543931  3213.000000  1158.000000  1745.000000   
247  47157021754   86700.406212  4402.000000  1512.000000  2502.000000   
248  47157021900   57704.207601  5708.000000   197.000000  5489.000000   
249  47157022022   30383.831631  7822.000000   203.000000  7146.000000   
250  47157022023   25694.713181  4486.000000   222.262593  4184.357910   
251  47157022024   22859.473987  3991.000000   197.737407  3722.642090   
252  47157022111   38607.322436  6574.000000   382.000000  6053.000000   
253  47157022112   40986.327748  6705.000000   265.000000  6335.000000   
254  47157022121   31321.209113  4411.000000   377.024822  3980.182495   
255  47157022122   34473.922068  4855.000000   414.975178  4380.817505   
256  47157022130   58698.461790  6448.000000   485.000000  5874.000000   
257  47157022210   43647.747529  5179.998652    87.999977  5013.998695   
258  47157022220   33399.747363  4688.001348   117.000023  4566.001305   
259  47157022310   34205.225991  6365.000000    22.000000  6317.000000   
260  47157022321   46662.222313  3846.000000   138.000000  3708.000000   
261  47157022322   62101.981201  4724.000000    78.000000  4597.000000   
262  47157022330   44659.304454  5670.000000   103.000000  5343.000000   
263  47157022

In [25]:
pd.read_excel('UDP_NY_2016_7.13.19_selectedNYNJcounties.xlsx')

geo_fips  TOD  downtown   empd02   hh_90         hinc90   hu_90  \
0     34003001000  1.0         0   6992.0  1885.0  143455.805452  1859.0   
1     34003002100  0.0         0    296.0   540.0  193072.663642   542.0   
2     34003002200  0.0         0   5320.0  1595.0  104392.349596  1563.0   
3     34003002300  0.0         0      NaN     NaN  116808.899868     NaN   
4     34003003100  0.0         0      NaN     NaN   89807.249814     NaN   
5     34003003200  0.0         0      NaN     NaN   66941.400411     NaN   
6     34003003300  0.0         0      NaN     NaN   94558.257817     NaN   
7     34003003401  0.0         0     44.0   836.0   91770.839485   829.0   
8     34003003402  0.0         0      NaN     NaN   96268.984734     NaN   
9     34003003500  0.0         0    145.0  1497.0   67763.069836  1482.0   
10    34003004001  0.0         0      NaN     NaN   84282.691740     NaN   
11    34003004002  0.0         0      NaN     NaN   84282.688605     NaN   
12    34003005000  0.0         0  15075.0  2180.0   72215.460543  2192.0   
13    34003006100  0.0         0    805.0  2503.0   69721.170544  2483.0   
14    34003006201  0.0         0      NaN     NaN   78986.458207     NaN   
15    34003006202  0.0         0      NaN     NaN   78986.459424     NaN   
16    34003006300  0.0         0    519.0  2738.0   70551.993112  2732.0   
17    34003007001  0.0         0      NaN     NaN  114475.654092     NaN   
18    34003007002  0.0         0      NaN     NaN  114475.651308     NaN   
19    34003008000  0.0         0   2316.0  2540.0  110399.397113  2537.0   
20    34003009100  0.0         0    728.0  1578.0  124696.638998  1571.0   
21    34003009200  0.0         0    750.0  1110.0  133453.078824  1112.0   
22    34003010100  0.0         0      NaN     NaN   93803.643279     NaN   
23    34003010200  0.0         0   1105.0  1450.0   76289.531059  1457.0   
24    34003010300  0.0         0      NaN     NaN   91428.356854     NaN   
25    34003011100  0.0         0    893.0  1632.0   68729.311459  1673.0   
26    34003011200  0.0         0    894.0  1669.0   74018.009966  1687.0   
27    34003011300  0.0         0   2713.0  1456.0   69626.009713  1461.0   
28    34003011400  1.0         0   3343.0  1912.0   67839.929649  1936.0   
29    34003012001  1.0         0      NaN     NaN   62064.450413     NaN   
...           ...  ...       ...      ...     ...            ...     ...   
3822  36119014100  1.0         0      NaN     NaN   56473.419265     NaN   
3823  36119014200  0.0         0      NaN     NaN   67594.429175     NaN   
3824  36119014300  0.0         0      NaN     NaN   37201.636122     NaN   
3825  36119014400  0.0         0      NaN     NaN   83138.261499     NaN   
3826  36119014500  0.0         0      NaN     NaN   84787.060122     NaN   
3827  36119014604  0.0         0      NaN     NaN   84761.939610     NaN   
3828  36119014605  1.0         0      NaN     NaN   66085.949525     NaN   
3829  36119014606  0.0         0      NaN     NaN  162226.081073     NaN   
3830  36119014607  0.0         0      NaN     NaN  107053.549021     NaN   
3831  36119014701  0.0         0      NaN     NaN  109566.287258     NaN   
3832  36119014703  0.0         0      NaN     NaN  106520.638359     NaN   
3833  36119014704  0.0         0      NaN     NaN   91499.998068     NaN   
3834  36119014804  0.0         0      NaN     NaN  101115.083560     NaN   
3835  36119014805  0.0         0      NaN     NaN  139835.795822     NaN   
3836  36119014806  0.0         0      NaN     NaN  117700.109497     NaN   
3837  36119014808  0.0         0      NaN     NaN  129908.048093     NaN   
3838  36119014809  0.0         0      NaN     NaN  100471.157634     NaN   
3839  36119014810  0.0         0      NaN     NaN   96713.673035     NaN   
3840  36119014811  0.0         0      NaN     NaN   96713.667412     NaN   
3841  36119014901  0.0         0      NaN     NaN  144145.198047     NaN   
3842  36119014903  0.0         0      NaN     NaN  116937

In [28]:
pd.read_stata('hhinc_singleregion.dta')

trtid10        hinc_00        hinc_90  hinc_16
0    28033070101   26255.709055   21379.569260  39318.0
1    28033070102   34183.920552   27835.857764  63229.0
2    28033070210   79501.087837   10224.314184  51865.0
3    28033070221   42015.009727   27959.579557  46250.0
4    28033070222   19446.971405   12941.307009  52349.0
5    28033070310   57698.443809   53749.999771  41217.0
6    28033070322   58913.163057   28069.748158  48750.0
7    28033070323   17604.728319    7968.176810  47853.0
8    28033070324   24204.421468   10936.859138  37565.0
9    28033070325   15830.067217    7152.875529  40316.0
10   28033070411   18057.463635   16904.802916  38661.0
11   28033070412   42942.192270   40201.066677  37057.0
12   28033070421   27299.415126   32039.710620  49904.0
13   28033070422   28219.022141   33118.999636  40409.0
14   28033070520   89312.845116   94065.305134  82715.0
15   28033070521   31678.904839   34118.115764  44306.0
16   28033070522   35748.820539   38501.405825  58279.0
17   28033070610   73442.242746    4226.857836  35247.0
18   28033070620   92957.002861   22418.356193  72324.0
19   28033070630   92817.450009   44295.631503  95357.0
20   28033070710   87636.646772   12625.903376  69258.0
21   28033070721   39375.488447   25837.345640  87431.0
22   28033070722   38552.801438   25354.361485  90759.0
23   28033070811   50734.363193    8816.256475  61895.0
24   28033070812   33812.621083    5862.510714  60299.0
25   28033070821   36427.938704    3666.486423  64048.0
26   28033070822   38035.140773    3826.523350  58616.0
27   28033070830   90335.918267   35603.395169  81023.0
28   28033070900   67822.254379   46478.073427  60734.0
29   28033071000   83919.546521   64968.370162  82453.0
..           ...            ...            ...      ...
241  47157021745   97546.540366   60539.257970  71984.0
242  47157021746   37719.524914   44693.078294  39901.0
243  47157021747   34538.258495   40923.661409  50423.0
244  47157021751  108909.739273   10507.147175  77308.0
245  47157021752  103310.214957    8462.414805  67820.0
246  47157021753   77851.543931    4195.362990  67054.0
247  47157021754   86700.406212    5243.383250  49353.0
248  47157021900   57704.207601   61831.827548  37763.0
249  47157022022   30383.831631   35740.478089  16316.0
250  47157022023   25694.713181   25974.714859  41719.0
251  47157022024   22859.473987   23108.579584  50238.0
252  47157022111   38607.322436   40420.000121  31725.0
253  47157022112   40986.327748   47144.825995  31593.0
254  47157022121   31321.209113   30504.425043  64115.0
255  47157022122   34473.922068   33574.922684  34911.0
256  47157022130   58698.461790   64851.477581  45552.0
257  47157022210   43647.747529   41373.467355  30500.0
258  47157022220   33399.747363   31496.575938  29329.0
259  47157022310   34205.225991   30658.999716  23059.0
260  47157022321   46662.222313   29286.996332  32995.0
261  47157022322   62101.981201   28439.572214  34674.0
262  47157022330   44659.304454   42278.347792  33262.0
263  47157022410   48260.233756   42627.956652  45781.0
264  47157022500   85024.275856   86882.631558  41308.0
265  47157022600  262707.893747  123600.734832  36589.0
266  47157022700   84144.164283   43435.606963  26465.0
267  47157980100   38379.622946   48985.244662      NaN
268  47157980200     552.116874     647.223899      NaN
269  47157980300            NaN            NaN      NaN
270  47157980400      18.425485       0.191090      NaN

[271 rows x 4 columns]